In [0]:
from pyspark.sql.functions import col, year, quarter, month, dayofmonth, date_format, lit, current_timestamp
from delta.tables import *
from pyspark.sql.functions import col, year, quarter, month, dayofmonth, date_format, lit, current_timestamp, split, explode

#  Providing storage account key to databricks
storage_account_name = "datalakecineanalytics"
account_key = "my_account_key" 

#  Authenticating with storage account
spark.conf.set(f"fs.azure.account.key.{storage_account_name}.dfs.core.windows.net", account_key)

# Using hive_metastore catalog 
catalog = "hive_metastore"
source_table = "silver.big_fat_table"
target_schema = "gold"

# Storing files in silver container in azure
gold_base_path = f"abfss://gold@{storage_account_name}.dfs.core.windows.net/"

print("Setup complete and Data Lake is connected")

✅ Setup Complete & Data Lake Connected!


In [0]:
# --- CELL 2: LOAD SILVER & BUILD DIMENSIONS ---
print("Loading Silver Data...")
df_silver = spark.read.table(f"{catalog}.{source_table}")

# DIMENSION 1: MOVIES & GENRES
print("Building dim_movies_genres...")
df_dim_movies = (df_silver
    .select("MovieID", "Title", "Musical_Themes", "MPAA_Rating", "Legs", "Director", "Actor_1", "Actor_2", "Actor_3", "Genres")
    .dropDuplicates(["MovieID"])
    .withColumn("Genre", explode(split(col("Genres"), r"\|")))
    .drop("Genres")
    .withColumn("ingest_date", current_timestamp())
)
(df_dim_movies.write.format("delta").mode("overwrite").option("overwriteSchema", "true")
    .option("path", f"{gold_base_path}dim_movies_genres/") 
    .saveAsTable(f"{catalog}.{target_schema}.dim_movies_genres"))


# DIMENSION 2: USERS
print("Building dim_users_enriched...")
df_dim_users = (df_silver
    .select("UserID", "Gender", "Age", "Occupation", "Zip_code", "State", "Region") 
    .dropDuplicates(["UserID"])
    .withColumn("ingest_date", current_timestamp())
)
(df_dim_users.write.format("delta").mode("overwrite").option("overwriteSchema", "true")
    .option("path", f"{gold_base_path}dim_users_enriched/") 
    .saveAsTable(f"{catalog}.{target_schema}.dim_users_enriched"))


# DIMENSION 3: TIME
print("Building dim_time...")
df_dim_time = (df_silver.select(col("Release_Date").alias("full_date")).distinct().filter("full_date IS NOT NULL")
    .withColumn("date_key", date_format("full_date", "yyyyMMdd").cast("int"))
    .withColumn("year", year("full_date"))
    .withColumn("quarter", quarter("full_date"))
    .withColumn("month", month("full_date"))
    .withColumn("day", dayofmonth("full_date"))
    .withColumn("day_name", date_format("full_date", "EEEE"))
    .withColumn("month_name", date_format("full_date", "MMMM"))
)
(df_dim_time.write.format("delta").mode("overwrite").option("overwriteSchema", "true")
    .option("path", f"{gold_base_path}dim_time/") 
    .saveAsTable(f"{catalog}.{target_schema}.dim_time"))

print("All dimensions are created")

Loading Silver Data...
Building dim_movies_genres...
Building dim_users_enriched...
Building dim_time...
✅ All Dimensions Created!


In [0]:
# --- CELL 3: BUILD FACT TABLE ---
print("Building fact_movie_performance...")

df_fact = (df_silver
    .withColumn("ReleaseDateKey", date_format("Release_Date", "yyyyMMdd").cast("int"))
    .select(
        "MovieID",
        "UserID",
        col("ReleaseDateKey").alias("Release_Date_FK"),
        "Rating",
        "Production_Budget_USD",
        "Domestic_Gross_USD",
        "Worldwide_Gross_USD",
        (col("Worldwide_Gross_USD") - col("Production_Budget_USD")).alias("Profit_USD")
    )
    .filter("MovieID IS NOT NULL AND UserID IS NOT NULL")
)

(df_fact.write
    .format("delta")
    .mode("overwrite")
    .option("overwriteSchema", "true")
    .option("path", f"{gold_base_path}fact_movie_performance/") 
    .saveAsTable(f"{catalog}.{target_schema}.fact_movie_performance")
)

print("Gold Layer (Star Schema) creation is complete")

Building fact_movie_performance...
✅ Gold Layer (Star Schema) Creation Complete! Your data is officially ready for Visualization.


In [0]:
%sql
SELECT * FROM hive_metastore.gold.dim_movies_genres

MovieID Title Musical_Themes MPAA_Rating Legs Director Actor_1 Actor_2 Actor_3 Genre ingest_date 1580 Men in Black (1997) null PG-13for language and sci-fi violence 4.91 Barry Sonnenfeld Tommy Lee Jones Will Smith Linda Fiorentino Action 2026-02-23T11:51:17.922Z 1580 Men in Black (1997) null PG-13for language and sci-fi violence 4.91 Barry Sonnenfeld Tommy Lee Jones Will Smith Linda Fiorentino Adventure 2026-02-23T11:51:17.922Z 1580 Men in Black (1997) null PG-13for language and sci-fi violence 4.91 Barry Sonnenfeld Tommy Lee Jones Will Smith Linda Fiorentino Comedy 2026-02-23T11:51:17.922Z 1580 Men in Black (1997) null PG-13for language and sci-fi violence 4.91 Barry Sonnenfeld Tommy Lee Jones Will Smith Linda Fiorentino Sci-Fi 2026-02-23T11:51:17.922Z 1959 Out of Africa (1985) null PG 12.16 Sydney Pollack Meryl Streep Robert Redford Klaus Maria Brandauer Drama 2026-02-23T11:51:17.922Z 1959 Out of Africa (1985) null PG 12.16 Sydney Pollack Meryl Streep Robert Redford Klaus Maria Brandauer Romance 2026-02-23T11:51:17.922Z 3175 Galaxy Quest (1999) null PGfor some action violence, mild language and sensuality 7.36 Dean Parisot Tim Allen Sigourney Weaver Alan Rickman Adventure 2026-02-23T11:51:17.922Z 3175 Galaxy Quest (1999) null PGfor some action violence, mild language and sensuality 7.36 Dean Parisot Tim Allen Sigourney Weaver Alan Rickman Comedy 2026-02-23T11:51:17.922Z 3175 Galaxy Quest (1999) null PGfor some action violence, mild language and sensuality 7.36 Dean Parisot Tim Allen Sigourney Weaver Alan Rickman Sci-Fi 2026-02-23T11:51:17.922Z 1591 Spawn (1997) null PG-13for thematic elements involving the demonic underworld, violence, intense fantasy action and crude humor. 2.79 Mark A.Z. Dippé Michael Jai White Martin Sheen John Leguizamo Action 2026-02-23T11:51:17.922Z 1591 Spawn (1997) null PG-13for thematic elements involving the demonic underworld, violence, intense fantasy action and crude humor. 2.79 Mark A.Z. Dippé Michael Jai White Martin Sheen John Leguizamo Adventure 2026-02-23T11:51:17.922Z 1591 Spawn (1997) null PG-13for thematic elements involving the demonic underworld, violence, intense fantasy action and crude humor. 2.79 Mark A.Z. Dippé Michael Jai White Martin Sheen John Leguizamo Sci-Fi 2026-02-23T11:51:17.922Z 1591 Spawn (1997) null PG-13for thematic elements involving the demonic underworld, violence, intense fantasy action and crude humor. 2.79 Mark A.Z. Dippé Michael Jai White Martin Sheen John Leguizamo Thriller 2026-02-23T11:51:17.922Z 1645 Devil's Advocate, The (1997) null null null Taylor Hackford Keanu Reeves Al Pacino Charlize Theron Crime 2026-02-23T11:51:17.922Z 1645 Devil's Advocate, The (1997) null null null Taylor Hackford Keanu Reeves Al Pacino Charlize Theron Horror 2026-02-23T11:51:17.922Z 1645 Devil's Advocate, The (1997) null null null Taylor Hackford Keanu Reeves Al Pacino Charlize Theron Mystery 2026-02-23T11:51:17.922Z 1645 Devil's Advocate, The (1997) null null null Taylor Hackford Keanu Reeves Al Pacino Charlize Theron Thriller 2026-02-23T11:51:17.922Z 471 Hudsucker Proxy, The (1994) null null null Joel Coen Tim Robbins Jennifer Jason Leigh Paul Newman Comedy 2026-02-23T11:51:17.922Z 471 Hudsucker Proxy, The (1994) null null null Joel Coen Tim Robbins Jennifer Jason Leigh Paul Newman Romance 2026-02-23T11:51:17.922Z 2366 King Kong (1933) null PG-13for frightening adventure violence and some disturbing images. 4.35 null null null null Action 2026-02-23T11:51:17.922Z 2366 King Kong (1933) null PG-13for frightening adventure violence and some disturbing images. 4.35 null null null null Adventure 2026-02-23T11:51:17.922Z 2366 King Kong (1933) null PG-13for frightening adventure violence and some disturbing images. 4.35 null null null null Horror 2026-02-23T11:51:17.922Z 1088 Dirty Dancing (1987) null null null null null null null Musical 2026-02-23T11:51:17.922Z 1088 Dirty Dancing (1987) null null null null null null null Romance 2026-02-23T11:51:17.922Z 496 What Happened Was... (199

In [0]:
%sql
SELECT * FROM hive_metastore.gold.dim_time

full_date date_key year quarter month day day_name month_name 1975-01-01 19750101 1975 1 1 1 Wednesday January 1976-01-01 19760101 1976 1 1 1 Thursday January 1973-01-01 19730101 1973 1 1 1 Monday January 1978-01-01 19780101 1978 1 1 1 Sunday January 1971-01-01 19710101 1971 1 1 1 Friday January 1977-01-01 19770101 1977 1 1 1 Saturday January 1987-01-01 19870101 1987 1 1 1 Thursday January

In [0]:
%sql
SELECT * FROM hive_metastore.gold.dim_users_enriched

UserID Gender Age Occupation Zip_code State Region ingest_date 148 M 50 17 57747 Unknown Unknown 2026-02-23T11:51:23.497Z 463 M 25 7 55105 MN Midwest 2026-02-23T11:51:23.497Z 471 M 35 7 08904 Unknown Unknown 2026-02-23T11:51:23.497Z 496 M 18 4 55455 MN Midwest 2026-02-23T11:51:23.497Z 833 M 35 7 46825 Unknown Unknown 2026-02-23T11:51:23.497Z 1088 F 1 10 98103 WA West 2026-02-23T11:51:23.497Z 1238 F 35 20 11215 Unknown Unknown 2026-02-23T11:51:23.497Z 1342 M 35 0 94560 Unknown Unknown 2026-02-23T11:51:23.497Z 1580 F 18 4 76201 Unknown Unknown 2026-02-23T11:51:23.497Z 1591 M 50 7 26501 Unknown Unknown 2026-02-23T11:51:23.497Z 1645 F 18 9 62225 Unknown Unknown 2026-02-23T11:51:23.497Z 243 M 25 16 11576 Unknown Unknown 2026-02-23T11:51:23.497Z 392 M 18 7 20037 Unknown Unknown 2026-02-23T11:51:23.497Z 540 M 18 1 15213 Unknown Unknown 2026-02-23T11:51:23.497Z 623 M 25 17 60555 IL Midwest 2026-02-23T11:51:23.497Z 737 M 1 19 53711 Unknown Unknown 2026-02-23T11:51:23.497Z 858 M 35 14 10013 Unknown Unknown 2026-02-23T11:51:23.497Z 897 M 25 6 92130 Unknown Unknown 2026-02-23T11:51:23.497Z 1025 M 25 16 34677 Unknown Unknown 2026-02-23T11:51:23.497Z 1084 M 1 19 03226 Unknown Unknown 2026-02-23T11:51:23.497Z 1127 M 25 0 11788 Unknown Unknown 2026-02-23T11:51:23.497Z 1395 M 25 2 07026 Unknown Unknown 2026-02-23T11:51:23.497Z 1460 F 18 4 95132 Unknown Unknown 2026-02-23T11:51:23.497Z 1483 M 18 4 54481 Unknown Unknown 2026-02-23T11:51:23.497Z 1507 M 35 17 95476 Unknown Unknown 2026-02-23T11:51:23.497Z 1522 M 35 20 10025 Unknown Unknown 2026-02-23T11:51:23.497Z 1721 M 18 19 70043 Unknown Unknown 2026-02-23T11:51:23.497Z 31 M 56 7 06840 Unknown Unknown 2026-02-23T11:51:23.497Z 516 F 56 14 55033 MN Midwest 2026-02-23T11:51:23.497Z 1139 M 25 1 93420-2852 Unknown Unknown 2026-02-23T11:51:23.497Z 1143 M 50 7 94024 Unknown Unknown 2026-02-23T11:51:23.497Z 1270 M 25 6 12230 Unknown Unknown 2026-02-23T11:51:23.497Z 1303 M 25 19 94111 Unknown Unknown 2026-02-23T11:51:23.497Z 1322 M 56 0 94043 Unknown Unknown 2026-02-23T11:51:23.497Z 1339 M 35 18 85275 Unknown Unknown 2026-02-23T11:51:23.497Z 1352 M 35 20 94122 Unknown Unknown 2026-02-23T11:51:23.497Z 1618 M 50 0 44139 Unknown Unknown 2026-02-23T11:51:23.497Z 1650 M 25 19 94607 Unknown Unknown 2026-02-23T11:51:23.497Z 1699 F 25 19 98102 WA West 2026-02-23T11:51:23.497Z 85 M 18 4 94945 Unknown Unknown 2026-02-23T11:51:23.497Z 137 F 45 6 78758 Unknown Unknown 2026-02-23T11:51:23.497Z 251 M 56 17 55105 MN Midwest 2026-02-23T11:51:23.497Z 451 M 56 13 54720 Unknown Unknown 2026-02-23T11:51:23.497Z 580 M 1 10 08534 Unknown Unknown 2026-02-23T11:51:23.497Z 808 M 25 7 85226 Unknown Unknown 2026-02-23T11:51:23.497Z 1265 F 18 20 49321 Unknown Unknown 2026-02-23T11:51:23.497Z 65 M 35 12 55803 MN Midwest 2026-02-23T11:51:23.497Z 458 M 50 16 55405-2546 MN Midwest 2026-02-23T11:51:23.497Z 883 F 35 14 92673 Unknown Unknown 2026-02-23T11:51:23.497Z 879 M 45 16 92018 Unknown Unknown 2026-02-23T11:51:23.497Z 1223 M 25 2 60102 IL Midwest 2026-02-23T11:51:23.497Z 53 M 25 0 96931 Unknown Unknown 2026-02-23T11:51:23.497Z 255 M 35 0 85310 Unknown Unknown 2026-02-23T11:51:23.497Z 481 M 45 7 55115 MN Midwest 2026-02-23T11:51:23.497Z 588 F 25 11 23220 Unknown Unknown 2026-02-23T11:51:23.497Z 799 F 25 5 98498 WA West 2026-02-23T11:51:23.497Z 804 M 25 20 90032 Unknown Unknown 2026-02-23T11:51:23.497Z 898 M 25 7 77005 Unknown Unknown 2026-02-23T11:51:23.497Z 970 M 25 0 27615 Unknown Unknown 2026-02-23T11:51:23.497Z 1157 M 45 7 30253 Unknown Unknown 2026-02-23T11:51:23.497Z 133 F 25 0 55071 MN Midwest 2026-02-23T11:51:23.497Z 296 M 50 5 89432 Unknown Unknown 2026-02-23T11:51:23.497Z 472 M 35 0 55418 MN Midwest 2026-02-23T11:51:23.497Z 853 M 25 17 55447 MN Midwest 2026-02-23T11:51:23.497Z 1466 M 18 4 29201 Unknown Unknown 2026-02-23T11:51:23.497Z 1718 M 18 4 43235 Unknown Unknown 2026-02-23T11:51:23.497Z 78 F 45 1 98029 WA West 2026-02-23T11:51:23.497Z 322 M 56 17 55117 MN Midwest 2026-02-23T11:51:23.497Z 513 M 25 0 55119 MN Midwest 2

In [0]:
%sql
SELECT * FROM hive_metastore.gold.fact_movie_performance

MovieID UserID Release_Date_FK Rating Production_Budget_USD Domestic_Gross_USD Worldwide_Gross_USD Profit_USD 2949 3589 null 4 1000000 16067035 59567035 58567035 1097 3589 null 1 10500000 439454989 797307407 786807407 3791 3590 null 4 24000000 51802742 62989834 38989834 588 3590 null 5 182000000 355559216 1046587513 864587513 1 3590 null 5 30000000 192523233 365270951 335270951 1270 3590 null 5 19000000 215612287 388862657 369862657 2640 3590 null 5 55000000 134218018 300200000 245200000 296 3590 null 5 8000000 107928762 212891598 204891598 480 3590 null 4 63000000 415404543 1058454230 995454230 1198 3590 null 5 20000000 225686079 367451914 347451914 1380 3590 null 3 6000000 188620000 394278547 388278547 1721 3590 null 4 200000000 674460013 2223048786 2023048786 1907 3590 null 4 200000000 0 69973540 -130026460 3578 3590 null 4 103000000 187683805 451683599 348683599 2949 3590 null 4 1000000 16067035 59567035 58567035 1097 3590 null 4 10500000 439454989 797307407 786807407 296 3591 null 5 8000000 107928762 212891598 204891598 480 3591 null 4 63000000 415404543 1058454230 995454230 1387 3591 null 4 12000000 273661595 484351938 472351938 1721 3591 null 3 200000000 674460013 2223048786 2023048786 356 3591 null 5 55000000 330151138 679835137 624835137 3578 3591 null 5 103000000 187683805 451683599 348683599 1 3592 null 5 30000000 192523233 365270951 335270951 1270 3592 null 5 19000000 215612287 388862657 369862657 296 3592 null 5 8000000 107928762 212891598 204891598 1380 3592 null 5 6000000 188620000 394278547 388278547 1721 3592 null 5 200000000 674460013 2223048786 2023048786 356 3592 null 5 55000000 330151138 679835137 624835137 3578 3592 null 5 103000000 187683805 451683599 348683599 1097 3592 null 4 10500000 439454989 797307407 786807407 588 3593 null 2 182000000 355559216 1046587513 864587513 1 3593 null 5 30000000 192523233 365270951 335270951 1270 3593 null 3 19000000 215612287 388862657 369862657 356 3593 null 5 55000000 330151138 679835137 624835137 588 3594 null 3 182000000 355559216 1046587513 864587513 1 3594 null 5 30000000 192523233 365270951 335270951 296 3594 null 5 8000000 107928762 212891598 204891598 1198 3594 null 5 20000000 225686079 367451914 347451914 1387 3594 null 3 12000000 273661595 484351938 472351938 356 3594 null 5 55000000 330151138 679835137 624835137 2949 3594 null 4 1000000 16067035 59567035 58567035 1097 3594 null 3 10500000 439454989 797307407 786807407 1270 3595 null 4 19000000 215612287 388862657 369862657 1198 3595 null 5 20000000 225686079 367451914 347451914 1387 3595 null 5 12000000 273661595 484351938 472351938 356 3595 null 4 55000000 330151138 679835137 624835137 1 3596 null 5 30000000 192523233 365270951 335270951 1198 3596 null 4 20000000 225686079 367451914 347451914 588 3597 null 4 182000000 355559216 1046587513 864587513 1 3597 null 5 30000000 192523233 365270951 335270951 1721 3597 null 5 200000000 674460013 2223048786 2023048786 356 3597 null 3 55000000 330151138 679835137 624835137 2640 3598 null 1 55000000 134218018 300200000 245200000 480 3598 null 1 63000000 415404543 1058454230 995454230 1721 3598 null 1 200000000 674460013 2223048786 2023048786 1097 3598 null 1 10500000 439454989 797307407 786807407 1 3599 null 4 30000000 192523233 365270951 335270951 480 3599 null 5 63000000 415404543 1058454230 995454230 356 3599 null 5 55000000 330151138 679835137 624835137 3791 3600 null 3 24000000 51802742 62989834 38989834 588 3600 null 3 182000000 355559216 1046587513 864587513 1 3600 null 5 30000000 192523233 365270951 335270951 1270 3600 null 4 19000000 215612287 388862657 369862657 296 3600 null 1 8000000 107928762 212891598 204891598 1380 3600 null 4 6000000 188620000 394278547 388278547 1721 3600 null 4 200000000 674460013 2223048786 2023048786 356 3600 null 5 55000000 330151138 679835137 624835137 1097 3600 null 4 10500000 439454989 797307407 786807407 3791 3601 null 4 24000000 51802742 62989834 38989834 1 3601 null 5 30000000 192523233 365270951 335270951 1270 3601 null 5 190